In [1]:
import tensorflow as tf
mnist = tf.keras.datasets.mnist
import numpy as np

In [2]:
(x_train, y_train),(x_test, y_test) = mnist.load_data()
x_train, x_test = x_train / 255.0, x_test / 255.0

In [3]:
import sys
sys.path.append('../')
import pfv_utils.utils as pu
reload(pu)

<module 'pfv_utils.utils' from '../pfv_utils/utils.py'>

In [4]:
def flatten(z):
    return tf.reshape(z, [-1, np.prod(z.shape[1:])])

In [6]:
tf.matmul


<function tensorflow.python.ops.math_ops.matmul>

In [7]:
class Net:
    def __init__(self):
        conv_dim = 3
        self.input = tf.placeholder(tf.float32, [None, 28,28,1])
        self.y = tf.placeholder(tf.int64, [None])
        
        self.layer0_vars = {}
        self.layer0_out = pu.conv_and_relu(self.input, [conv_dim,conv_dim,1,32], out_dict=self.layer0_vars)
        self.layer1_vars = {}
        self.layer1_out = pu.conv_and_relu(self.layer0_out, [conv_dim,conv_dim,32,32], out_dict = self.layer1_vars)
        
        self.other_vars = {}

        self.layer1_flattened = flatten(self.layer1_out)
        print 'shape of: self.layer1_flattened: ' + str(self.layer1_flattened)
        self.S = tf.placeholder(tf.float32, [self.layer1_flattened.shape[1], None])
        
        self.final_W = tf.Variable(tf.truncated_normal([self.layer1_flattened.shape[1].value,10], stddev=0.1))
        self.final_b = tf.Variable(tf.constant(0.0, shape = [10]))
        
        print 'shape of: tf.matmul(self.layer1_flattened, self.final_W): ' + str(tf.matmul( self.layer1_flattened, self.final_W).shape)
        
        # TODO: needs to be self.layer1_flattened * matrix 
        
        self.mat_mul_result = (tf.matmul( self.layer1_flattened, self.final_W) - 
                              
                              
                              
                              tf.matmul(tf.matmul(tf.matmul(self.layer1_flattened, self.S), tf.transpose(self.S)),
                                   self.final_W))
        
        print str(self.mat_mul_result.shape)
        self.output_logits =  self.mat_mul_result+  self.final_b

        #self.output_logits = pu.add_ip(self.layer1_flattened,10, out_dict = self.other_vars)

        
        self.loss = tf.reduce_sum(tf.nn.sparse_softmax_cross_entropy_with_logits(labels=self.y,
                                                                                 logits = self.output_logits))
        
        self.pred_labels = tf.argmax(self.output_logits, axis = 1)
        self.accuracy = tf.reduce_mean(tf.cast(tf.equal(self.pred_labels, self.y), tf.float32))
        
        assert(self.loss.shape.as_list() == [])
        assert(self.pred_labels.shape.as_list() == [None]), 'Pred labels: ' + str(self.pred_labels.shape)
        assert(self.accuracy.shape.as_list() == [])
        assert(self.output_logits.shape.as_list() == [None, 10])
        

In [8]:
net = Net()

shape of: self.layer1_flattened: Tensor("Reshape:0", shape=(?, 25088), dtype=float32)
shape of: tf.matmul(self.layer1_flattened, self.final_W): (?, 10)
(?, 10)


In [9]:
train_step = tf.train.AdamOptimizer(1e-4).minimize(net.loss)

In [10]:
config = tf.ConfigProto()
config.gpu_options.allow_growth = True
sess = tf.Session(config=config)
sess.run(tf.global_variables_initializer())

In [11]:
batch_size = 16
it = -1

In [12]:
batch_start_idx = -16

In [13]:
S_default = np.zeros((25088,1))

In [14]:
while it < 10000:
    it+=1
    batch_start_idx = (batch_start_idx + batch_size) % (x_train.shape[0])
    
    batch_end_idx = batch_start_idx + batch_size
    
    batch_x = np.expand_dims(x_train[batch_start_idx:batch_end_idx, :,:],3)
    batch_y = y_train[batch_start_idx:batch_end_idx]
    
    
    batch_loss, batch_accuracy,batch_pred_labels,_ = sess.run([net.loss, net.accuracy, 
                                                               net.pred_labels, train_step], 
                                                              feed_dict= {net.input: batch_x, net.y: batch_y,
                                                                         
                                                                         net.S :S_default})
    
    if it % 1000 == 0:
        print 'On iteration: %d; loss: %0.2f; accuracy: %0.2f' % (it, batch_loss, batch_accuracy)
        if it == 10000:
            break
        
    
    
    

On iteration: 0; loss: 66.71; accuracy: 0.25
On iteration: 1000; loss: 5.93; accuracy: 0.81
On iteration: 2000; loss: 2.38; accuracy: 0.88
On iteration: 3000; loss: 4.23; accuracy: 0.94
On iteration: 4000; loss: 3.48; accuracy: 0.94
On iteration: 5000; loss: 0.37; accuracy: 1.00
On iteration: 6000; loss: 5.75; accuracy: 0.88
On iteration: 7000; loss: 4.01; accuracy: 0.94
On iteration: 8000; loss: 1.78; accuracy: 0.94
On iteration: 9000; loss: 0.60; accuracy: 1.00
On iteration: 10000; loss: 0.25; accuracy: 1.00


https://stackoverflow.com/questions/35298326/freeze-some-variables-scopes-in-tensorflow-stop-gradient-vs-passing-variables

In [18]:
# Idxs of items we don't want to change in training
perm_idxs = np.arange(0,10)
perm_X = x_train[perm_idxs,:,:]
perm_Y = y_train[perm_idxs]
feed_dict  = {net.input: np.expand_dims(perm_X,3), net.S: S_default}
# Get current layer1 activations
perm_layer1_activations = sess.run(net.layer1_flattened, feed_dict = feed_dict)
perm_output_logits = sess.run(net.output_logits, feed_dict = feed_dict)

In [19]:
import scipy.linalg

In [20]:
S=scipy.linalg.orth(perm_layer1_activations.T)

In [27]:
opt2 = tf.train.AdamOptimizer(1e-4)
train_step2 = opt2.minimize(net.loss, var_list=[net.final_W])
sess.run(tf.variables_initializer(opt2.variables()))

In [28]:
 batch_loss, batch_accuracy,batch_pred_labels,_ = sess.run([net.loss, net.accuracy, 
                                                               net.pred_labels, train_step2], 
                                                              feed_dict= {net.input: batch_x, net.y: batch_y,
                                                                         
                                                                         net.S :S})

In [36]:
batch_x.shape

(16, 28, 28, 1)

In [33]:
perm_layer1_activations2 = sess.run(net.layer1_flattened, feed_dict = {)


In [34]:
np.max(np.abs(perm_layer1_activations-perm_layer1_activations2))

ValueError: operands could not be broadcast together with shapes (10,25088) (16,25088) 

In [ ]:
optimizer = tf.train.AdamOptimizer()
sess.run(tf.variables_initializer(optimizer.variables()))

In [ ]:
#np.dot(S.T, np.dot(S,perm_layer1_activations)) - perm_layer1_activations

In [103]:
# Want to restrict 

In [104]:
perm_layer1_activations.shape

(10, 25088)

In [26]:
z=sess.run(net.pred_labels, feed_dict = {net.input: np.expand_dims(perm_X,3)})

In [28]:
perm_Y

array([5, 0, 4, 1, 9, 2, 1, 3, 1, 4], dtype=uint8)

In [19]:
batch_y

array([7, 7, 0, 0, 1, 3, 9, 1, 5, 6, 6, 8, 8, 4, 5, 1], dtype=uint8)

In [20]:
batch_pred_labels

array([7, 7, 0, 0, 1, 3, 9, 1, 5, 6, 6, 8, 8, 4, 5, 1])

In [21]:
np.mean(batch_y == batch_pred_labels)

1.0

In [22]:
batch_accuracy

1.0